### **Sample 3 Model**: Extending NovelTM Dataset


This notebook is a clean version of the logistic regression classification process and error review for Sample 3 of fiction/non-fiction training data. Many steps that went into the general process (assembling the sample using sampling logic, getting the EF data for the sample, exploding the EF files into one corpus DataFrame) are not included. Instead, checkpoint data will be loaded in this notebook in order to train and test the classifier and review errors.

Sample 3 is a sample of English-language fiction that has the same number of volumes for fiction (53) and non-fiction (211) for each decade reflected in volumes added to HTDL since 2016.

First, import our libraries:

In [1]:
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
import pandas as pd
pd.options.display.max_columns = None
import numpy as np
from sklearn.linear_model import LogisticRegression
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.naive_bayes import MultinomialNB
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import f1_score
from sklearn.model_selection import cross_validate
from pathlib import Path
import math, random
from htrc_features import FeatureReader, Volume
import os

#### Loading the train/test data

The sample used to train/test this predictive model were developed in notebook `samp3-fiction-lr-clean.ipynb`. As such, we can simply load three TSVs and start to train/test the model. These TSVs are one each with metadata corresponding to a fiction (`f_df3`) and a non-fiction sample (`nf_df3`), and the last is a corpus DataFrame (`corpus3`) made up of our volumes, their tokens and their ground truth data (whether or not they have been tagged as fiction or non-fiction).

Before loading our data, I will define a function to fix any legacy HTIDs that had two forms: one for the filename HTID (which substituted `=` and `+` for `:` and `/`) and one for the actual HTID (which included `:` and `/`). This function will be used on the metadata TSVs after we load them.

In [19]:
def ark_fix(st: str):
    replace = {43: 58, 61:47}
    return st.translate(replace)

In [2]:
# Takes ~100 SECONDS to run
corpus_df3 = pd.read_csv('3-corpus-df-8878.tsv', sep='\t')
corpus_df3 = corpus_df3.rename(columns={'class': 'true_class'})
print(corpus_df3.shape)

corpus_df3.head()

(8876, 4)


htid  fold  \
0        nyp.33433074851936     0   
1  uc2.ark+=13960=t4xg9gm5s     0   
2        inu.30000091583363     0   
3        mdp.39015020936194     0   
4        mdp.39015063931714     0   

                                              tokens true_class  
0  ['0', '0', '0', '0', '0', '0', '0', '074851', ...          f  
1  ['0', '0', '0', '0', '0', '0', '0', '00', '000...         nf  
2  ['0', '0', '0', '0', '0', '001', '0010', '0017...         nf  
3  ['0', '0', '0', '0', '0', '0', '0', '0', '0', ...         nf  
4  ['0', '0', '1', '1', '1', '1', '1', '1', '1', ...          f

The next step is to generate a term-doc matrix for our volumes. This matrix has one volume per row (doc) and then one column for each of 5,000 features (terms/words) in our dataset. We can adjust the number of features considering each time we generate the matrix, and the more features considered, the longer it will take to create the matrix. Lastly, we save the matrix to CSV for archival purposes.

#### OPTIONAL: Correcting ground truth after human review
After human review of the errors for this sample, we have identified 45 volume IDs with misclassified ground truth, as agreed upon by two different reviewers. We ingest the text file with the HTIDs that need correction, and then add them to a list.

In [32]:
errors = []

with open('/Users/rdubnic2/Desktop/samp3_gt_correction_htids.txt', 'r') as f:
    ids = f.read().splitlines()
    for id in ids:
        id = ark_fix(id)
        errors.append(id)

print(type(errors))
print(errors)
print(len(errors))

<class 'list'>
['uc1.31970033858793', 'dul1.ark:/13960/t4hm5zs2h', 'umn.319510021342121', 'njp.32101068168630', 'uc1.31175035237117', 'umn.319510024581580', 'hvd.hwjr4h', 'nyp.33433075968358', 'osu.32435022458699', 'dul1.ark:/13960/t15m6qx0w', 'uc1.aa0000462499', 'hvd.32044090308453', 'uiuo.ark:/13960/t3dz10b96', 'ucm.532430713x', 'dul1.ark:/13960/t0ms4mx49', 'uc2.ark:/13960/t3fx7567r', 'hvd.32044090075011', 'nnc1.0043354602', 'hvd.32044024276016', 'dul1.ark:/13960/t3vt2js1t', 'uiug.30112049778704', 'coo.31924027381577', 'pst.000006683368', 'osu.32435055434898', 'dul1.ark:/13960/t7jq1nt3c', 'loc.ark:/13960/t86h5511x', 'njp.32101067646669', 'uiug.30112069647771', 'dul1.ark:/13960/t9z03vs2q', 'hvd.hwjrj5', 'aeu.ark:/13960/t5t731g58', 'inu.30000099040424', 'umn.31951p00302290d', 'dul1.ark:/13960/t58d0nd8w', 'osu.32435020172110', 'uiug.30112104348153', 'osu.32435019648013', 'hvd.hnp7kv', 'mdp.39015005886851', 'nyp.33433000745004', 'hvd.hn1f5l', 'uiug.30112003411037', 'uva.x030826058', 'hvd

Now look through our corpus_df dataframe to find the HTIDs in our list and switch their ground truth (it doesn't matter the original value, we simply know it needs to change to the opposite class):

In [26]:
# 'dul1.ark:/13960/t4hm5zs2' in errors
'njp.3210106816863' in errors

True

In [35]:
new_df = corpus_df3.loc[ark_fix(corpus_df3['htid']).isin(errors)]
print(new_df.shape)

AttributeError: 'Series' object has no attribute 'translate'

In [36]:
corpus_df3.head()
print(corpus_df3.shape)

n = 0

for t in corpus_df3.itertuples():
    idx = t[0]
    vol_class = t.true_class
    vol_id = ark_fix(t.htid)

    if vol_id in errors and vol_class == 'f':
        corpus_df3.at[idx, 'true_class'] = 'nf'
        n += 1

    if vol_id in errors and vol_class == 'nf':
        corpus_df3.at[idx, 'true_class'] = 'f'
        n += 1
    
    else:
        continue

print(f"Corrected ground truth for {n} volumes")

# Only need to save once
# corpus_df3.to_csv('3-corpus-df-8878_CORRECTED.tsv')

(8876, 4)
Corrected ground truth for 45 volumes


#### Training the Model
The first step to trainig the model is to generate a term-doc matrix for our volumes. This matrix has one volume per row (doc) and then one column for each of 5,000 features (terms/words) in our dataset. We can adjust the number of features considering each time we generate the matrix, and the more features considered, the longer it will take to create the matrix. Lastly, we save the matrix to CSV for archival purposes.

In [37]:
# Takes ~10 MINUTES to run
vectorizer = CountVectorizer(max_features = 5000)

sparse_wordcounts = vectorizer.fit_transform(corpus_df3.tokens)
wordcounts = sparse_wordcounts.toarray()

corpus_words = pd.DataFrame(wordcounts, columns = [vectorizer.get_feature_names_out()])
corpus_words.head()

corpus_words.to_csv('3_corpus_words_matrix_CORRECTED.tsv', sep='\t')

# UNCOMMENT TO LOAD FILES AND SKIP ABOVE STEPS (ALSO COMMENT OUT ALL CODE ABOVE):
# corpus_words = pd.read_csv('3_corpus_words_matrix.tsv', sep='\t', index_col=0)
# corpus_words.head()

In order to better balance our dataset, we are considering volume length in the classification process. We do this by first creating a new column with the count of tokens/words per volume:

In [38]:
vol_lengths = corpus_df3['tokens'].str.len()
vol_lengths

0        482485
1       1400049
2       6201352
3        781332
4        411228
         ...   
8871     413574
8872    2785838
8873     602546
8874    1403119
8875      96644
Name: tokens, Length: 8876, dtype: int64

Next, we divide each feature count per volume by the total number of tokens in the volume. This helps convey that 5 counts of a given token is more important to a volume with 10,000 total tokens than to one with 100,000 tokens.

In [39]:
wordfreqs = corpus_words.divide(vol_lengths, axis = 'rows')
wordfreqs['vol_length'] = vol_lengths

# wordfreqs.to_csv('3_wordfreqs_matrix_CORRECTED.tsv', sep='\t')

# IF LOADING FILES TO REPRODUCE:
# wordfreqs = pd.read_csv('3_wordfreqs_matrix.tsv', sep='\t', index_col=0)
# # wordfreqs['vol_length'] = vol_lengths

wordfreqs.head(10)

00           000            01            02            03  \
0  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
1  7.142607e-07  7.142607e-07  1.428521e-06  0.000000e+00  0.000000e+00   
2  0.000000e+00  0.000000e+00  9.675310e-07  0.000000e+00  1.612552e-07   
3  0.000000e+00  0.000000e+00  2.559731e-06  0.000000e+00  0.000000e+00   
4  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
5  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
6  4.468101e-07  0.000000e+00  0.000000e+00  2.234050e-07  1.787240e-06   
7  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
8  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
9  3.364189e-05  2.587838e-06  0.000000e+00  7.763513e-06  7.763513e-06   

             04            05            06            07   08            09  \
0  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.0  0.000000e+00   
1  7.142607e-07  0.000000e+00  7.142607e-07  0.000000e+00  0.0  0.000000e+00   
2  1.612552e-07  0.000000e+00  0.000000e+00  1.612552e-07  0.0  1.612552e-07   
3  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.0  0.000000e+00   
4  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.0  0.000000e+00   
5  2.146084e-06  0.000000e+00  0.000000e+00  0.000000e+00  0.0  0.000000e+00   
6  0.000000e+00  4.468101e-07  2.234050e-07  2.234050e-07  0.0  0.000000e+00   
7  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.0  0.000000e+00   
8  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.0  0.000000e+00   
9  5.175675e-06  1.035135e-05  7.763513e-06  5.175675e-06  0.0  2.587838e-06   

             10       100          1000           101           102       103  \
0  1.658083e-05  0.000000  0.000000e+00  2.072603e-06  2.072603e-06  0.000002   
1  1.428521e-05  0.000005  1.142817e-05  1.428521e-06  7.142607e-07  0.000000   
2  1.854434e-05  0.000010  1.612552e-07  1.773807e-06  1.935062e-06  0.000001   
3  3.839597e-05  0.000000  0.000000e+00  0.000000e+00  1.279866e-06  0.000001   
4  2.431741e-06  0.000002  0.000000e+00  2.431741e-06  2.431741e-06  0.000002   
5  0.000000e+00  0.000000  0.000000e+00  2.146084e-06  2.146084e-06  0.000002   
6  2.055326e-05  0.000005  6.702151e-07  0.000000e+00  1.117025e-06  0.000001   
7  9.162443e-07  0.000000  0.000000e+00  9.162443e-07  0.000000e+00  0.000000   
8  2.440572e-05  0.000009  0.000000e+00  3.050715e-06  3.050715e-06  0.000003   
9  1.526824e-04  0.000018  2.587838e-06  1.293919e-05  5.175675e-06  0.000013   

            104           105           106           107           108  \
0  0.000000e+00  2.072603e-06  2.072603e-06  2.072603e-06  0.000000e+00   
1  7.142607e-07  7.142607e-07  0.000000e+00  7.142607e-07  0.000000e+00   
2  1.290041e-06  3.708869e-06  1.773807e-06  2.580083e-06  2.257572e-06   
3  2.559731e-06  2.559731e-06  0.000000e+00  1.279866e-06  2.559731e-06   
4  2.431741e-06  2.431741e-06  2.431741e-06  2.431741e-06  0.000000e+00   
5  0.000000e+00  0.000000e+00  2.146084e-06  2.146084e-06  0.000000e+00   
6  1.117025e-06  4.468101e-07  6.702151e-07  2.234050e-07  4.468101e-07   
7  9.162443e-07  9.162443e-07  0.000000e+00  1.832489e-06  0.000000e+00   
8  6.101430e-06  0.000000e+00  6.101430e-06  3.050715e-06  3.050715e-06   
9  7.763513e-06  7.763513e-06  1.811486e-05  1.811486e-05  7.763513e-06   

            109          10th        11           110           111  \
0  2.072603e-06  0.000000e+00  0.000000  0.000000e+00  0.000000e+00   
1  1.428521e-06  7.142607e-07  0.000005  0.000000e+00  7.142607e-07   
2  1.935062e-06  2.257572e-06  0.000010  4.031379e-06  1.935062e-06   
3  1.279866e-06  0.000000e+00  0.000046  0.000000e+00  3.839597e-06   
4  0.000000e+00  0.000000e+00  0.000007  2.431741e-06  4.863482e-06   
5  2.146084e-06  0.000000e+00  0.000002  0.000000e+00  0.000000e+00   
6  1.563835e-06  3.351075e-06  0.000033  4.468101e-07  8.936201e-07   
7  9.162443e-07  0.0

Now, it's time to collect the train (8000) and test set (2000) data to feed to our predictive model. First, we shuffle the rows in order to create random sets, and then once again save the shuffled DataFrame to a CSV in case of code failure (as the random shuffling is not reproducible).

In [13]:
# wordfreqs = wordfreqs.sample(frac = 1)
# wordfreqs.to_csv('3_shuffled_word_freqs_CORRECTED.tsv', sep='\t')
# wordfreqs.head()

# # UNCOMMENT TO LOAD FILE AND SKIP STEPS ABOVE (ALSO COMMENT OUT ABOVE CODE):
# wordfreqs = pd.read_csv('3_shuffled_word_freqs_2.tsv', sep='\t', index_col=0)
# wordfreqs.head()

00  000   01        02        03   04   05   06   07   08  \
4105  0.000000  0.0  0.0  0.000000  0.000000  0.0  0.0  0.0  0.0  0.0   
3630  0.000000  0.0  0.0  0.000000  0.000000  0.0  0.0  0.0  0.0  0.0   
8576  0.000000  0.0  0.0  0.000000  0.000007  0.0  0.0  0.0  0.0  0.0   
1663  0.000000  0.0  0.0  0.000000  0.000000  0.0  0.0  0.0  0.0  0.0   
3915  0.000002  0.0  0.0  0.000002  0.000000  0.0  0.0  0.0  0.0  0.0   

            09        10       100 1000       101       102       103  \
4105  0.000000  0.000144  0.000000  0.0  0.000000  0.000000  0.000011   
3630  0.000000  0.000265  0.000044  0.0  0.000029  0.000033  0.000031   
8576  0.000007  0.000046  0.000000  0.0  0.000000  0.000000  0.000000   
1663  0.000000  0.000016  0.000002  0.0  0.000002  0.000002  0.000002   
3915  0.000000  0.000000  0.000000  0.0  0.000000  0.000002  0.000002   

           104       105       106       107       108       109      10th  \
4105  0.000000  0.000022  0.000000  0.000000  0.000000  0.000000  0.000000   
3630  0.000031  0.000025  0.000029  0.000027  0.000019  0.000027  0.000002   
8576  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
1663  0.000002  0.000002  0.000002  0.000002  0.000002  0.000002  0.000000   
3915  0.000000  0.000000  0.000004  0.000000  0.000000  0.000000  0.000000   

            11       110       111       112       113       114       115  \
4105  0.000100  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
3630  0.000073  0.000029  0.000017  0.000027  0.000012  0.000021  0.000019   
8576  0.000007  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
1663  0.000007  0.000002  0.000002  0.000002  0.000002  0.000002  0.000002   
3915  0.000006  0.000000  0.000000  0.000000  0.000000  0.000002  0.000002   

           116       117       118       119        12       120       121  \
4105  0.000000  0.000000  0.000000  0.000000  0.000066  0.000000  0.000000   
3630  0.000023  0.000027  0.000023  0.000023  0.000046  0.000027  0.000027   
8576  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
1663  0.000002  0.000002  0.000002  0.000000  0.000007  0.000002  0.000002   
3915  0.000002  0.000002  0.000002  0.000000  0.000004  0.000000  0.000000   

           122       123       124       125       126       127       128  \
4105  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
3630  0.000033  0.000035  0.000041  0.000033  0.000023  0.000033  0.000033   
8576  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
1663  0.000002  0.000002  0.000002  0.000002  0.000002  0.000002  0.000002   
3915  0.000002  0.000004  0.000004  0.000000  0.000002  0.000000  0.000002   

           129 12mo 12th        13       130       131       132       133  \
4105  0.000000  0.0  0.0  0.000066  0.000000  0.000000  0.000000  0.000000   
3630  0.000025  0.0  0.0  0.000029  0.000023  0.000015  0.000015  0.000010   
8576  0.000000  0.0  0.0  0.000000  0.000000  0.000000  0.000000  0.000000   
1663  0.000002  0.0  0.0  0.000007  0.000002  0.000002  0.000002  0.000002   
3915  0.000000  0.0  0.0  0.000002  0.000000  0.000000  0.000000  0.000000   

           134       135       136       137       138       139        14  \
4105  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000078   
3630  0.000027  0.000052  0.000052  0.000060  0.000019  0.000010  0.000033   
8576  0.000000  0.000000  0.000000  0.000000  0.000007  0.000007  0.000007   
1663  0.000004  0.000004  0.000002  0.000002  0.000002  0.000002  0.000007   
3915  0.000000  0.000002  0.000000  0.000002  0.000002  0.000002  0.000004   

           140       141       142       143       144       145       146  \
4105  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
3630  0.000008  0.000017  0.000021  0.000010  0.000008  0.000004  0.000004   
8576  0.000007  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
1663  0.

Next, we align our raw token data DataFrame, which contains the ground truth in the form of the `class` column, with our shuffled term-doc matrix in order to evaluate the results of the classifier.

In [40]:
shuffled_corpus_df = corpus_df3.loc[wordfreqs.index, : ]
shuffled_corpus_df.head()

htid  fold  \
0        nyp.33433074851936     0   
1  uc2.ark+=13960=t4xg9gm5s     0   
2        inu.30000091583363     0   
3        mdp.39015020936194     0   
4        mdp.39015063931714     0   

                                              tokens true_class  
0  ['0', '0', '0', '0', '0', '0', '0', '074851', ...          f  
1  ['0', '0', '0', '0', '0', '0', '0', '00', '000...         nf  
2  ['0', '0', '0', '0', '0', '001', '0010', '0017...         nf  
3  ['0', '0', '0', '0', '0', '0', '0', '0', '0', ...         nf  
4  ['0', '0', '1', '1', '1', '1', '1', '1', '1', ...          f

In [41]:
shuffled_corpus_df['true_class'].value_counts()

nf    7597
f     1279
Name: true_class, dtype: int64

We now take the first 2000 rows of our shuffled term-doc matrix and assign it to our test set, `testfreqs`, and also generate a corresponding list of ground truth for this set from the shuffled DF we created above.

In [42]:
testfreqs = wordfreqs.iloc[0: 2000, : ]
test_y = (shuffled_corpus_df['true_class'][0: 2000] == 'f').astype(int)

test_y[0:10]
print(len(test_y))

2000


We repeat this process for the training set.

In [43]:
trainfreqs = wordfreqs.iloc[2000 : , : ]
train_y = (shuffled_corpus_df['true_class'][2000: ] == 'f').astype(int) 

train_y[0:10]
print(len(train_y))

6876


Next we scale our data to try to balance numerical data differences between columns, first for our training set:

In [44]:
trainscaler = StandardScaler()
trainXscaled = trainscaler.fit_transform(trainfreqs)
trainXscaled = pd.DataFrame(trainXscaled, columns = trainfreqs.columns)
trainXscaled.head()

00       000        01        02        03        04        05  \
0  1.740829  1.240951  0.655710  0.144437  0.413270  1.180539  0.721624   
1 -0.078801 -0.055092 -0.096333 -0.058644 -0.086181 -0.108488 -0.114822   
2 -0.078801 -0.055092 -0.110334 -0.058644 -0.086181 -0.108488 -0.114822   
3 -0.078801 -0.055092 -0.110334 -0.058644 -0.086181 -0.108488 -0.114822   
4 -0.078801 -0.055092 -0.110334 -0.058644 -0.086181 -0.108488  0.229893   

         06        07        08        09        10       100      1000  \
0  0.950212  0.708771  0.214073  0.311607  0.587234  0.076144 -0.159244   
1 -0.097147 -0.105953 -0.057378 -0.079019 -0.333649 -0.149477 -0.159244   
2 -0.097147 -0.105953 -0.057378 -0.079019 -0.278040 -0.180425 -0.159244   
3 -0.097147 -0.105953 -0.057378 -0.079019 -0.335082 -0.144195 -0.159244   
4 -0.097147 -0.105953 -0.057378 -0.079019  0.129795  0.004614  1.628357   

        101       102       103       104       105       106       107  \
0  0.005364  0.741546  0.362994  0.622916  0.191952  0.151155  0.512772   
1 -0.140828 -0.225497 -0.230420 -0.258259 -0.194851 -0.230985 -0.284691   
2 -0.217705 -0.279020 -0.282312 -0.317993 -0.088396 -0.290128 -0.112950   
3 -0.037709 -0.279020 -0.282312 -0.317993 -0.035664 -0.013182 -0.027877   
4 -0.217705 -0.279020 -0.282312 -0.317993 -0.238076 -0.290128 -0.354426   

        108       109      10th        11       110       111       112  \
0  0.336259  0.710448 -0.259815  0.425812  0.377350  0.641133  0.649858   
1 -0.221598 -0.248825 -0.018467 -0.318302 -0.114979 -0.144866 -0.212988   
2 -0.081085 -0.317725 -0.259815 -0.357192 -0.182511 -0.165570 -0.268367   
3 -0.278654 -0.317725 -0.259815 -0.357192 -0.024397 -0.068622 -0.268367   
4 -0.278654 -0.317725 -0.259815 -0.025011 -0.182511  0.082005 -0.268367   

        113       114       115       116       117       118       119  \
0  0.856354  0.327724  0.512063  0.116320  0.689308  0.289005  0.439559   
1 -0.279637 -0.280955 -0.264902 -0.161358 -0.206887 -0.256746 -0.178852   
2 -0.089987 -0.364446 -0.338156 -0.054562 -0.081267 -0.341211 -0.229274   
3 -0.356645 -0.364446 -0.338156 -0.307380 -0.378645  0.054309 -0.229274   
4 -0.356645 -0.364446 -0.338156 -0.307380 -0.378645 -0.341211 -0.229274   

         12       120       121       122       123       124       125  \
0  0.468838  0.097172  0.022890  0.395237  0.065876  0.062310  0.469048   
1 -0.315529 -0.054385 -0.046306 -0.279489 -0.310683 -0.286090 -0.017776   
2  0.314974 -0.061758 -0.022931 -0.362590 -0.405434 -0.373755 -0.108327   
3 -0.277761 -0.027232 -0.011352 -0.362590  0.038252  0.447259 -0.036467   
4  0.480007 -0.061758 -0.055797 -0.362590 -0.405434  1.722866  0.392093   

        126       127       128       129      12mo      12th        13  \
0  0.546286  0.414915  0.228344  0.337089 -0.032247 -0.182603  0.493334   
1 -0.301447 -0.412520 -0.286202 -0.287629 -0.021021  0.253928 -0.357962   
2 -0.068138  0.278692 -0.061214  0.285282 -0.032247 -0.296732 -0.300381   
3  0.491048  0.054843 -0.377558  0.068434 -0.032247 -0.296732 -0.339547   
4  0.736676 -0.412520  0.714894 -0.384315 -0.032247 -0.296732  0.613355   

        130       131       132       133       134       135       136  \
0  0.267856  0.009844  0.224008  0.272978  0.335787  0.298730  0.469344   
1 -0.312318 -0.329597 -0.181996 -0.180613 -0.285317 -0.182096 -0.219854   
2 -0.391899 -0.329597 -0.237686 -0.236478 -0.381443 -0.070286  0.197824   
3 -0.391899  0.053859  0.023095 -0.236478  0.068686 -0.334973  0.039732   
4  0.559742 -0.329597  1.760178 -0.236478 -0.381443  0.579089  0.552567   

        137       138       139        14       140       141       142  \
0  0.353602  0.282354  0.373965  0.638596  0.551247 -0.139088  0.237064   
1 -0.403079 -0.292532 -0.384220 -0.339277 -0.245228 -0.294450 -0.166386   
2 -0.051909  0.312282 -0.384220 -0.196476 -0.310169 -0.398923 -0.378547   
3  0.546697  0.083358  1.043276 -0.334461 -0.310169  0.090290  0.118193   
4  0.809641 -0.394602 -0.3

And again for the test set:

In [45]:
testscaler = StandardScaler()
testXscaled = testscaler.fit_transform(testfreqs)
testXscaled = pd.DataFrame(testXscaled, columns = testfreqs.columns)
testXscaled.head()

00       000        01        02        03        04        05  \
0 -0.087971 -0.104818 -0.086907 -0.107598 -0.093117 -0.052632 -0.105258   
1 -0.086539 -0.083113 -0.067021 -0.107598 -0.093117 -0.041748 -0.105258   
2 -0.087971 -0.104818 -0.073439 -0.107598 -0.088669 -0.050175 -0.105258   
3 -0.087971 -0.104818 -0.051274 -0.107598 -0.093117 -0.052632 -0.105258   
4 -0.087971 -0.104818 -0.086907 -0.107598 -0.093117 -0.052632 -0.105258   

         06        07        08        09        10       100      1000  \
0 -0.057187 -0.059303 -0.051073 -0.102515 -0.251237 -0.220377 -0.173779   
1 -0.044047 -0.059303 -0.051073 -0.102515 -0.265536 -0.152434  0.974409   
2 -0.057187 -0.056466 -0.051073 -0.095204 -0.239007 -0.082325 -0.157577   
3 -0.057187 -0.059303 -0.051073 -0.102515 -0.115357 -0.220377 -0.173779   
4 -0.057187 -0.059303 -0.051073 -0.102515 -0.339368 -0.187332 -0.173779   

        101       102       103       104       105       106       107  \
0 -0.161689 -0.161272 -0.080295 -0.417980 -0.170776 -0.157569 -0.131725   
1 -0.227481 -0.313221 -0.170851 -0.332613 -0.309311 -0.420610 -0.232190   
2 -0.192211 -0.176658 -0.121532 -0.263797 -0.003896 -0.195490 -0.094192   
3 -0.373402 -0.249951 -0.114931 -0.112047 -0.121094 -0.420610 -0.190358   
4 -0.125003 -0.121098 -0.064604 -0.127345 -0.134148 -0.111990 -0.105163   

        108       109      10th        11       110       111       112  \
0 -0.397455 -0.137989 -0.204852 -0.384097 -0.363763 -0.200415 -0.131067   
1 -0.397455 -0.228434 -0.112306 -0.339651 -0.363763 -0.177526 -0.350480   
2 -0.106733 -0.157303  0.087660 -0.292356  0.059838 -0.138404 -0.009059   
3 -0.067823 -0.249309 -0.204852  0.025482 -0.363763 -0.077371 -0.350480   
4 -0.397455 -0.429033 -0.204852 -0.319247 -0.108245 -0.044559  0.164385   

        113       114       115       116       117       118       119  \
0 -0.137610 -0.110146 -0.155087 -0.106285 -0.101500 -0.108038 -0.128627   
1 -0.328988 -0.407091 -0.340439 -0.294169 -0.203191 -0.388120 -0.226647   
2 -0.111549 -0.083645 -0.239867 -0.125310 -0.160086 -0.148416 -0.223181   
3 -0.429621 -0.407091 -0.437903 -0.215935 -0.256663 -0.215165 -0.249271   
4 -0.087010 -0.058692 -0.106081 -0.392964 -0.074614 -0.059506 -0.073971   

         12       120       121       122       123       124       125  \
0 -0.284825 -0.232732 -0.131042 -0.132216 -0.132136 -0.138362 -0.143228   
1 -0.264674 -0.168380 -0.302034 -0.309550 -0.336854 -0.306743 -0.189875   
2 -0.236956 -0.217558 -0.249853 -0.255433 -0.079957 -0.195390 -0.188226   
3  0.055472 -0.402758 -0.230834 -0.402798 -0.444501 -0.236631 -0.293335   
4 -0.329265 -0.203270 -0.085833 -0.402798 -0.078010 -0.093843 -0.117218   

        126       127       128       129      12mo      12th        13  \
0 -0.139866 -0.093710 -0.134528 -0.112283 -0.077299 -0.127113 -0.263031   
1 -0.308636 -0.214087 -0.283537 -0.309601 -0.077299 -0.127113 -0.221093   
2 -0.257132 -0.148770 -0.273443 -0.085414 -0.077299 -0.071162 -0.108007   
3 -0.238361 -0.163963 -0.221490 -0.227439 -0.077299 -0.127113  0.047471   
4 -0.095244 -0.061883 -0.095131 -0.060114 -0.077299 -0.127113 -0.293504   

        130       131       132       133       134       135       136  \
0  0.056673 -0.101496 -0.112304 -0.113826  0.206058 -0.134037 -0.112615   
1 -0.240759 -0.266931 -0.304966 -0.335550 -0.400611  0.315468 -0.318575   
2  0.008901  0.333462 -0.063197 -0.083634 -0.164607 -0.210732 -0.133470   
3 -0.257035 -0.198045 -0.224743 -0.243225 -0.213297 -0.231893 -0.426876   
4 -0.130923 -0.057756 -0.061365 -0.452139 -0.400611  0.210469 -0.058161   

        137       138       139        14       140       141       142  \
0 -0.087573 -0.082762 -0.086628 -0.306707  0.095279 -0.083521 -0.081853   
1 -0.296394 -0.316093 -0.321429 -0.236581 -0.236608 -0.184315 -0.293758   
2  0.089603 -0.050988 -0.138278 -0.105357 -0.095926 -0.256457 -0.052997   
3 -0.209442  0.000916 -0.223660  0.139167 -0.098412 -0.207579 -0.405185   
4 -0.032362 -0.021070 -0.0

Our `C` parameter can affect results, so let's first find the optimal `C` value using a simple loop:

In [46]:
for c_param in [.00001, .0001, .001, .01, .1, 1, 10]:
    logist = LogisticRegression(C = c_param, max_iter = 1000, class_weight = 'balanced') 
    results = cross_validate(logist, trainXscaled, train_y, cv = 5, scoring = 'f1')
    print('C parameter:', c_param)
    print('Mean f1:', np.mean(results['test_score']))
    print()

C parameter: 1e-05
Mean f1: 0.7723561875889301

C parameter: 0.0001
Mean f1: 0.810711812607186

C parameter: 0.001
Mean f1: 0.8445973925351753

C parameter: 0.01
Mean f1: 0.8482236038963749

C parameter: 0.1
Mean f1: 0.8271842570344864

C parameter: 1
Mean f1: 0.8162332674266978

C parameter: 10
Mean f1: 0.8059991352915654



Next, we can run the next cell to train and test the classifier and generate final, first-round predicitons. After the above loop, we know that the optimal `C` parameter is `0.001` to get the best results and output errors for manual review.

We'll also generate cross-validated (5-fold) mean scores for P, R, and F1:

In [47]:
logist = LogisticRegression(C = .01, max_iter = 1000, class_weight = 'balanced') 
logist.fit(trainXscaled, train_y)
predictions = logist.predict(testXscaled)
print(f"Raw accuracy: {sum(predictions == test_y) / len(predictions)}")

tp = sum((test_y == 1) & (predictions == 1))
fp = sum((test_y == 0) & (predictions == 1))
fn = sum((test_y == 1) & (predictions == 0))

precision = tp / (tp + fp)
recall = tp / (tp + fn)

F1 = 2 * (precision * recall) / (precision + recall)

print(f"Precision: {round(precision, 4)}\nRecall: {round(recall, 4)}\nF1: {round(F1, 4)}\n")

# Also generate mean scores for P, R, F1 via 5-fold cross-validation:
lr_results_p = cross_validate(logist, trainXscaled, train_y, cv = 5, scoring = 'precision')
lr_results_r = cross_validate(logist, trainXscaled, train_y, cv = 5, scoring = 'recall')
lr_results_f1 = cross_validate(logist, trainXscaled, train_y, cv = 5, scoring = 'f1')

print(f"5-fold CV mean Precision: {round(np.mean(lr_results_p['test_score']), 4)}")
print(f"5-fold CV mean Recall: {round(np.mean(lr_results_r['test_score']), 4)}")
print(f"5-fold CV mean F1: {round(np.mean(lr_results_f1['test_score']), 4)}")

Raw accuracy: 0.952
Precision: 0.7853
Recall: 0.9207
F1: 0.8476

5-fold CV mean Precision: 0.7925
5-fold CV mean Recall: 0.913
5-fold CV mean F1: 0.8482


These scores are decent, but not the best when compared to our other samples, so we may end up going with one of those for the big crunch.

But first, part of evaluating this process though is examining the most important features for each class, which we can do by getting the coefficients and feature names from our trained model:

In [24]:
# logist = LogisticRegression(C = .001, max_iter = 1000, class_weight = 'balanced')
# logist.fit(trainXscaled, train_y)
coefficients = [x for x in zip(logist.coef_[0], vectorizer.get_feature_names_out())]

We'll first sort the feature names based on coefficients and then look at the top and bottom 20 for fiction. Here, the top 20 features are those most likely to indicate fictiop and the bottom are most likely to indicate not fiction. Remember, this is not a universal finding, but only valid for our train/test data:

Top 20 feature names:

In [25]:
coefficients.sort()
samp3_lr_top_fict_tokens = coefficients

for w in coefficients[:20]:
    print(f"{w}\n")

# with open('samp2_lr_top_10pct_fict_coeff.csv','w') as out:
#     csv_out=csv.writer(out)
#     csv_out.writerow(['value','feature'])

#     for row in coefficients[:500]:
#         csv_out.writerow(row)

(-0.04112973165666741, 'enter')

(-0.038196814213295696, 'siege')

(-0.037596018538407265, 'ha')

(-0.03631126686220827, 'ﬁnd')

(-0.035754419509676345, 'ihe')

(-0.0355946683036531, 'fashion')

(-0.034512922321263906, 'expedition')

(-0.02957639223168187, 'admiral')

(-0.02905268982803295, 'nicholas')

(-0.02873672173142846, 'conduct')

(-0.02838240627774152, 'aside')

(-0.02836279593877803, 'has')

(-0.02822937361442856, 'tlie')

(-0.027852654517103684, 'perfect')

(-0.027384731853768437, 'anne')

(-0.02734886496908002, 'advocate')

(-0.027133729137401273, 'goes')

(-0.026048551895944818, 'sir')

(-0.02583748536737604, 'cardinal')

(-0.025832314386873927, 'darkness')



Bottom 20 feature names

In [26]:
coefficients.sort(reverse=True)

for w in coefficients[:20]:
    print(f"{w}\n")

# with open('samp2_lr_bottom_10pct_fict_coeff.csv','w') as out:
#     csv_out=csv.writer(out)
#     csv_out.writerow(['value','feature'])

#     for row in coefficients[:500]:
#         csv_out.writerow(row)

(0.05620898626906967, 'talents')

(0.0538208040173439, 'could')

(0.05155437446899872, 'dreadful')

(0.05147893958603022, 'compare')

(0.05070557723021542, 'bull')

(0.04943573800608893, 'began')

(0.04420873871666642, 'had')

(0.04155196078253717, 'me')

(0.04142289661553159, 'took')

(0.04108435823832539, 'story')

(0.040748878165427674, 'curiosity')

(0.03990323906413646, 'answered')

(0.03938117162758839, 'said')

(0.03920603932734278, 'possibility')

(0.03795308711614309, 'sentiment')

(0.037293928347910996, 'au')

(0.036538387270154196, 'letter')

(0.0362736428225469, 'affair')

(0.03597245984783832, 'favourite')

(0.03563881321948887, 'generous')



#### Error Review
We will now cobble together the various data sources and classification results to generate DataFrames of errors and metadata to allow human reviewers to review each error and code them as types of errors. First, we start with a new DF with the prediction % for each volume in our test set:

In [27]:
t_rev_df = pd.DataFrame(logist.predict_proba(testXscaled), columns=logist.classes_)
print(t_rev_df.shape)

testX_id = wordfreqs.index[:2000]
t_rev_df['idx'] = testX_id

t_rev_df.head()

(2000, 2)


0         1   idx
0  0.998671  0.001329  4105
1  0.999207  0.000793  3630
2  0.999422  0.000578  8576
3  0.010870  0.989130  1663
4  0.029539  0.970461  3915

Add back in `HTID` and `true_class` columns for each volume:

In [28]:
rev_df_meta = shuffled_corpus_df[:2000]
rev_df_meta.head()

htid  fold  \
4105  pur1.32754065781688     0   
3630  uiug.30112119965496     0   
8576   osu.32437010221675     0   
1663   mdp.39015019374266     0   
3915   nyp.33433074913587     0   

                                                 tokens true_class  
4105  ['0', '0', '0', '0', '0', '0', '0', '1', '1', ...         nf  
3630  ['0', '0', '0', '0', '0', '0', '0', '0', '0', ...         nf  
8576  ['0', '03', '09', '1', '1', '1', '1', '1', '1'...         nf  
1663  ['0', '1', '1', '1', '1', '1', '1', '1', '1', ...          f  
3915  ['0', '00', '1', '1', '1', '1', '1', '1', '1',...          f

In [29]:
rev_df = pd.merge(t_rev_df, rev_df_meta, left_on='idx', right_index=True)
rev_df.rename(columns = {0:'nf_prob', 1:'f_prob', 'class':'true_class'}, inplace = True)
rev_df = rev_df.drop(columns=['tokens','fold'])
rev_df = rev_df.set_index('idx')

# Fix the ark IDs before we use them to grab HTF metadata
for tuple in rev_df.itertuples():
    idx = tuple[0]
    htid = ark_fix(tuple.htid)
    rev_df['htid'][idx] = htid

rev_df.head(10)

/var/folders/k9/cjwycg9j25503fvmwqtbz_dc0000gq/T/ipykernel_93714/4232065336.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  rev_df['htid'][idx] = htid


nf_prob    f_prob                      htid true_class
idx                                                          
4105  0.998671  0.001329       pur1.32754065781688         nf
3630  0.999207  0.000793       uiug.30112119965496         nf
8576  0.999422  0.000578        osu.32437010221675         nf
1663  0.010870  0.989130        mdp.39015019374266          f
3915  0.029539  0.970461        nyp.33433074913587          f
6204  0.126084  0.873916        mdp.39015065443189          f
7466  0.986398  0.013602        uc1.31175035161986         nf
5152  0.973163  0.026837  loc.ark:/13960/t6c25pv5b         nf
6937  0.997174  0.002826        mdp.39015056956397         nf
4607  0.556434  0.443566        uc1.31175035510661         nf

In [30]:
rev_df['true_class'].value_counts()

nf    1736
f      264
Name: true_class, dtype: int64

htid  fold  \
0        nyp.33433074851936     0   
1  uc2.ark+=13960=t4xg9gm5s     0   
2        inu.30000091583363     0   
3        mdp.39015020936194     0   
4        mdp.39015063931714     0   

                                              tokens true_class  
0  ['0', '0', '0', '0', '0', '0', '0', '074851', ...          f  
1  ['0', '0', '0', '0', '0', '0', '0', '00', '000...         nf  
2  ['0', '0', '0', '0', '0', '001', '0010', '0017...         nf  
3  ['0', '0', '0', '0', '0', '0', '0', '0', '0', ...         nf  
4  ['0', '0', '1', '1', '1', '1', '1', '1', '1', ...          f

In [33]:
vol_df3 = pd.read_csv('3-vol-df-htf-9355-2.tsv', sep='\t')
print(vol_df3.shape)

vol_df3.head(10)

(9355, 27)


htid access rights  ht_bib_key                description  \
0     uc1.c0000031880  allow     pd       58830           v.007 yr.1644-45   
1  ien.35556005146808  allow     pd      534433                  1609-1647   
2        chi.18173825  allow     pd      541172                v.4 1644-46   
3  mdp.39015063634334  allow     pd     1412584                        NaN   
4    mou.010005891476  allow     pd     1959888                        NaN   
5  mdp.39015068265712  allow     pd     1961336                        NaN   
6  mdp.39015011444398  allow     pd     1961353                        NaN   
7  mdp.39015069273640  allow     pd     1961540                        NaN   
8        uc1.b4343743  allow     pd     3911273  (Title) 26:pt.1:1501-1640   
9  osu.32435019510890  allow     pd     3915471                NO1601-1647   

  source      source_bib_num                             oclc_num isbn  \
0     UC             3831428                              6078250  NaN   
1    IEN              958695                              1199808  NaN   
2    CHI     2378884,2381589                    1751506,243889157  NaN   
3    MIU  990014125840106381                              4155441  NaN   
4    MOU           b19685506                              9693188  NaN   
5    MIU  990019613360106381                              9690829  NaN   
6    MIU  990019613530106381                             23638879  NaN   
7    MIU  990019615400106381                              5729768  NaN   
8     UC        GLAD135917-S  171550286,213945561,2786662,3525698  NaN   
9     OU           b11465347                              1774183  NaN   

   decade       issn             lccn  \
0    1640        NaN      sn 85062456   
1    1640  0080-8326         42043485   
2    1640        NaN      sn 85062623   
3    1640        NaN         40036604   
4    1640        NaN              NaN   
5    1640        NaN      lum92007893   
6    1640        NaN              NaN   
7    1640        NaN              NaN   
8    1640  1946-4975       2008251146   
9    1640  0083-0186  46006169 //r883   

                                               title  \
0                    Journals of the House of Lords.   
1  Contributions - Scripps Institution of Oceanog...   
2                  Journals of the House of Commons.   
3               A treatise of the covenant of grace:   
4  Romes cruelty & apostacie declared in a sermon...   
5  A sermon preached to the honourable House of C...   
6  A sermon preached before the Honourable House ...   
7  A sermon preached to the honorable House of Co...   
8  The Code of Federal regulations of the United ...   
9      Treaties and other international acts series.   

                                             imprint rights_reason_code  \
0                                           H.M.S.O.                bib   
1                Scripps Institution of Oceanography                bib   
2                  By order of the House of Commons,                bib   
3        Printed by G. Miller for E. Brewster, 1645.                bib   
4  Printed by George Miller for Tho. Underhill, 1...                bib   
5  Printed for Robert Bostock, dwelling at the si...                bib   
6              Printed by I. Okes, for S. Man, 1641.                bib   
7             Printed by M. F. for J. Bartlet, 1642.                bib   
8                                 U.S. G.P.O., 1939-                bib   
9  Dept. of State, For sale by the Supt. of Docs....                bib   

      rights_timestamp  us_gov_doc_flag  rights_date_used pub_place lang  \
0  2017-04-13 03:25:10              0.0              1645       enk  eng   
1  2017-05-01 06:27:32              0.0              1647       cau  eng   
2  2017-05-01 06:28:56              0.0              1646       enk  eng   
3  2008-07-17 00:30:05              0.0              1645       enk  eng   
4  2018-01-14 03:25:20              0.0              1645       enk 

In [39]:
final_rev_df = pd.merge(rev_df, vol_df3, how='inner', on='htid')

print(final_rev_df.shape)
final_rev_df.head()

# final_rev_df.tail(50)

(1993, 30)


nf_prob    f_prob                 htid true_class access rights  \
0  0.998671  0.001329  pur1.32754065781688         nf  allow     pd   
1  0.999207  0.000793  uiug.30112119965496         nf  allow   pdus   
2  0.999422  0.000578   osu.32437010221675         nf  allow     pd   
3  0.010870  0.989130   mdp.39015019374266          f   deny     ic   
4  0.029539  0.970461   nyp.33433074913587          f  allow     pd   

   ht_bib_key description source      source_bib_num  \
0    11340972         NaN    PUR              863522   
1   101737150         NaN    UIU             2295272   
2     9526644   1950 1950     OU           b11751824   
3     1726860         NaN    MIU  990017268600106381   
4     7688858        v. 2    NYP          b131410039   

                     oclc_num        isbn  decade       issn            lccn  \
0                    31911762  0160463939    1990        NaN             NaN   
1                     6363414         NaN    1940        NaN     e  47000021   
2  175309330,2394728,45856932         NaN    1950  0148-5229  17009090//r862   
3                    27088801         NaN    1940        NaN        43000564   
4                    16111550         NaN    1750        NaN             NaN   

                                               title  \
0  Kansas and Missouri Metropolitan Culture Distr...   
1  Guide to occupational choice and training ; su...   
2  Annual report of the Attorney General of the U...   
3                              Soviet short stories.   
4        The invisible spy, by Exploralibus [pseud.]   

                                             imprint rights_reason_code  \
0  U.S. G.P.O. : For sale by the U.S. G.P.O., Sup...                bib   
1                                              1947]                gfv   
2  U.S. Dept. of Justice, Office of the Attorney ...                bib   
3                            The Pilot press, [1942]                bib   
4                                     Gardner, 1755.                bib   

      rights_timestamp  us_gov_doc_flag  rights_date_used pub_place lang  \
0  2012-07-21 19:30:23              1.0              1994       dcu  eng   
1  2019-09-29 01:04:30              0.0              1947       dcu  eng   
2  2016-12-11 03:25:12              1.0              1950       dcu  eng   
3  2008-09-13 21:30:23              0.0              1942       enk  eng   
4  2010-10-07 20:32:05              0.0              1755       enk  eng   

  bib_fmt collection_code content_provider_code responsible_entity_code  \
0      BK             PUR                purdue                  purdue   
1      BK            UIUC              illinois                illinois   
2      SE             OSU                   osu                     osu   
3      BK             MIU                 umich                   umich   
4      BK             NYP                  nypl                    nypl   

  digitization_agent_code access_profile_code  \
0                  google              google   
1                  google              google   
2                  google              google   
3                  google              google   
4                  google              google   

                                              author  
0  United States. Congress. House. Committee on t...  
1                      Greenleaf, Walter J. b. 1889.  
2               United States. Department of Justice  
3                                                NaN  
4                 Haywood, Eliza Fowler, 1693?-1756.

Now, we pull only a few metadata columns (author, title, year of publication) and combine with our results in order to make human review of mistakes easier. We exclude columns by index number, making this slightly confusing:

In [40]:
# columns we want: [nf_prob, f_prob, htid, true_class, title, pub_date, author]

cols1 = list(final_rev_df.columns[4:15])
# print(cols1)

cols2 = list(final_rev_df.columns[16:20])
# print(cols2)

cols3 = list(final_rev_df.columns[21:29])
# print(cols3)

cols4 = list(final_rev_df.columns[30:])
# print(cols4)

drop_columns = cols1 + cols2 + cols3 + cols4

final_rev_df = final_rev_df.drop(columns=drop_columns)

final_rev_df.head(10)

nf_prob    f_prob                      htid true_class  \
0  0.998671  0.001329       pur1.32754065781688         nf   
1  0.999207  0.000793       uiug.30112119965496         nf   
2  0.999422  0.000578        osu.32437010221675         nf   
3  0.010870  0.989130        mdp.39015019374266          f   
4  0.029539  0.970461        nyp.33433074913587          f   
5  0.126084  0.873916        mdp.39015065443189          f   
6  0.986398  0.013602        uc1.31175035161986         nf   
7  0.973163  0.026837  loc.ark:/13960/t6c25pv5b         nf   
8  0.997174  0.002826        mdp.39015056956397         nf   
9  0.556434  0.443566        uc1.31175035510661         nf   

                                               title  rights_date_used  \
0  Kansas and Missouri Metropolitan Culture Distr...              1994   
1  Guide to occupational choice and training ; su...              1947   
2  Annual report of the Attorney General of the U...              1950   
3                              Soviet short stories.              1942   
4        The invisible spy, by Exploralibus [pseud.]              1755   
5  Dialogues of the dead; together with some fabl...              1754   
6  The book of common-prayer and administration o...              1713   
7        New York of to-day, by Henry Collins Brown.              1917   
8  Applied quaternionic analysis / Vladislav V. K...              2003   
9  Father and son : or, The rock of Charbonniére ...              1860   

                                              author  
0  United States. Congress. House. Committee on t...  
1                      Greenleaf, Walter J. b. 1889.  
2               United States. Department of Justice  
3                                                NaN  
4                 Haywood, Eliza Fowler, 1693?-1756.  
5  Fénelon, François de Salignac de La Mothe-, 16...  
6                                 Church of England.  
7                        Brown, Henry Collins, 1862-  
8                           Kravchenko, Vladislav V.  
9                       Fitzball, Edward, 1792-1873.

Save the full set of results to a TSV in case we want to consult them in the future:

In [41]:
final_rev_df.to_csv('3_results_review_3.tsv', sep='\t', index=False)

Last, we need to find mistakes--rows where the `true_class` column value `nf` and `f_prob` is under 0.5, and vice versa. We'll also find and return any rows with equal `f_prob` and `nf_prob` values (though I haven't found any results like this yet!):

In [42]:
mistakes = final_rev_df.loc[((final_rev_df['nf_prob'] > 0.5) & (final_rev_df['true_class'] == 'f')) 
                            | ((final_rev_df['f_prob'] > 0.5) & (final_rev_df['true_class'] == 'nf')) 
                            | (final_rev_df['f_prob'] == final_rev_df['nf_prob'])]


print(f"There were {mistakes.shape[0]} mistakes out of {final_rev_df.shape[0]} volumes, or {((mistakes.shape[0])/(final_rev_df.shape[0]))*100}%")
mistakes.head()


There were 103 mistakes out of 1993 volumes, or 5.168088309081787%


nf_prob    f_prob                       htid true_class  \
11  0.110787  0.889213         uc1.31970033858793         nf   
13  0.633607  0.366393         mdp.39015069176819          f   
53  0.317524  0.682476  dul1.ark:/13960/t4hm5zs2h         nf   
68  0.233210  0.766790         mdp.39015011940171         nf   
81  0.017687  0.982313        umn.319510021342121         nf   

                                                title  rights_date_used  \
11  Cecilia ; or, Memoirs of an heiress / by Miss ...              1784   
13  The works of Jonathan Swift ... accurately rev...              1755   
53  The history of Jemmy and Jenny Jessamy : in th...              1753   
68                                    The Adventurer.              1793   
81                               The little minister.              1910   

                                author  
11            Burney, Fanny, 1752-1840  
13         Swift, Jonathan, 1667-1745.  
53  Haywood, Eliza Fowler, 1693?-1756.  
68                                 NaN  
81            Barrie, J. M. 1860-1937.

Last, we add a column with a link back to each volume in the HTDL to make review easier:

In [43]:
# add a link back to the item:
mistakes['url'] = 'https://babel.hathitrust.org/cgi/pt?id='

mistakes['url'] = mistakes['url'] + mistakes['htid']
mistakes.head()

/var/folders/k9/cjwycg9j25503fvmwqtbz_dc0000gq/T/ipykernel_93714/3235859113.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  mistakes['url'] = 'https://babel.hathitrust.org/cgi/pt?id='
/var/folders/k9/cjwycg9j25503fvmwqtbz_dc0000gq/T/ipykernel_93714/3235859113.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  mistakes['url'] = mistakes['url'] + mistakes['htid']


nf_prob    f_prob                       htid true_class  \
11  0.110787  0.889213         uc1.31970033858793         nf   
13  0.633607  0.366393         mdp.39015069176819          f   
53  0.317524  0.682476  dul1.ark:/13960/t4hm5zs2h         nf   
68  0.233210  0.766790         mdp.39015011940171         nf   
81  0.017687  0.982313        umn.319510021342121         nf   

                                                title  rights_date_used  \
11  Cecilia ; or, Memoirs of an heiress / by Miss ...              1784   
13  The works of Jonathan Swift ... accurately rev...              1755   
53  The history of Jemmy and Jenny Jessamy : in th...              1753   
68                                    The Adventurer.              1793   
81                               The little minister.              1910   

                                author  \
11            Burney, Fanny, 1752-1840   
13         Swift, Jonathan, 1667-1745.   
53  Haywood, Eliza Fowler, 1693?-1756.   
68                                 NaN   
81            Barrie, J. M. 1860-1937.   

                                                  url  
11  https://babel.hathitrust.org/cgi/pt?id=uc1.319...  
13  https://babel.hathitrust.org/cgi/pt?id=mdp.390...  
53  https://babel.hathitrust.org/cgi/pt?id=dul1.ar...  
68  https://babel.hathitrust.org/cgi/pt?id=mdp.390...  
81  https://babel.hathitrust.org/cgi/pt?id=umn.319...

In [45]:
# Save final mistakes TSV to file
mistakes.to_csv('3_mistakes_4.tsv', sep='\t')

# Save final full classification results TSV to file
final_rev_df.to_csv('3_pred_review_4.tsv', sep='\t')